In [ ]:
http://minio-api-triton-inference-services.apps.nebula.sl/audio/record_out%20(1).wav

In [1]:
import requests
import json
from io import BytesIO
import librosa
import numpy as np
from IPython.display import Audio


In [2]:
# Define the Triton server endpoint
triton_url = "http://triton-route-triton-inference-services.apps.nebula.sl/v2/models/whisper-large-v3/infer"

# Audio URL
audio_url = "http://minio-api-triton-inference-services.apps.nebula.sl/audio/record_out%20(1).wav"


In [6]:
# Step 1: Download the audio file from the URL
response = requests.get(audio_url)
if response.status_code != 200:
    print(f"Failed to download audio from {audio_url}. Status code: {response.status_code}")
    exit(1)

# Step 2: Process the audio
# Load the audio content into librosa
audio_data, sample_rate = librosa.load(BytesIO(response.content), sr=None)

target_sample_rate = 16000  # or 48000 depending on the model
if sample_rate != target_sample_rate:
    audio_data = librosa.resample(y=audio_data, orig_sr=sample_rate, target_sr=target_sample_rate)
    print(f"Resampled Audio to {target_sample_rate} Hz")
else:
    print("Audio is already at the target sample rate.")

Resampled Audio to 16000 Hz


In [7]:
audio_data

array([0.0000000e+00, 7.2759576e-11, 2.9103830e-11, ..., 4.4440402e-04,
       8.3447271e-04, 2.1367602e-04], dtype=float32)

In [4]:
Audio(audio_data, rate=sample_rate)


In [8]:
audio_data = audio_data.astype(np.float32)  

In [9]:
audio_tensor = audio_data.tobytes()
# print(audio_tensor)

b'\x00\x00\x00\x00\x00\x00\xa0.\x00\x00\x00.\x00\x00\x00/\x00\x00\xf0.\x00\x00@/\x00\x00\x18/\x00\x000/\x00\x00 /\x00\x00`.\x00\x00\x00.\x00\x00\xb0.\x00\x00\x00\xae\x00\x00`/\x00\x00\xc0\xaf\x00\x00\x80/\x00\x00\xf0\xaf\x00\x00 0\x00\x00 \xb0\x00\x00X0\x00\x00L\xb0\x00\x00\x930\x00\x00\x92\xb0\x00\x00\xc60\x00\xc0\xbb\xb0\x00\x00\xe20\x00\x00\xc4\xb0\x00\x00\xf00\x00\x00\xb6\xb0\x00\x00\xbc0\x00\x00,\xb0\x00\x00\x90/\x00\x00\x180\x00\x00\xe4\xb0\x00\x80Q1\x00\xc0\xa2\xb1\x00\x00\xec1\x00\x00"\xb2\x00\x00U2\x00\x80\x88\xb2\x00@\xaa2\x00\x80\xd0\xb2\x00\x00\xf92\x00@\x12\xb3\x00\xe0\'3\x00\xe0>\xb3\x00`T3\x00\x18h\xb3\x00\xe0w3\x00\x80\x81\xb3\x00\xc0\x833\x00`\x81\xb3\x00\x00s3\x00`V\xb3\x00`*3\x00\xc0\xd9\xb2\x00\x80\xdc1\x00 \x952\x00\xa0G\xb3\x00\x14\xae3\x00\xc0\x01\xb4\x00\xd014\x00`g\xb4\x00\x88\x904\x00\x14\xaf\xb4\x00\x80\xce4\x00(\xee\xb4\x00b\x065\x00\xac\x14\xb5\x00=!5\x00T+\xb5\x00=25\x00\xf34\xb5\x00\xd425\x00\xec*\xb5\x00\x80\x1c5\x00\xbe\x06\xb5\x00\x18\xd24\x00\xc8\x85\

In [10]:
payload = {
    "inputs": [
        {
            "name": "INPUT",
            "shape": [1, len(audio_data)],  # Shape of the tensor: [batch_size, length of audio data]
            "datatype": "FP32",  # Make sure the datatype matches the input configuration
            "data": audio_data.tolist()  # Converting numpy array to list for JSON serialization
        }
    ],
    "outputs": [
        {
            "name": "OUTPUT"
        }
    ]
}

# Step 4: Send the POST request to Triton
headers = {"Content-Type": "application/json"}
response = requests.post(triton_url, json=payload, headers=headers)

# Step 5: Handle the response
if response.status_code == 200:
    response_data = response.json()

else:
    print(f"Error with Triton request. Status code: {response.status_code}")
    print(f"Error message: {response.text}")


In [11]:
response_data

{'model_name': 'whisper-large-v3',
 'model_version': '1',
 'outputs': [{'name': 'OUTPUT',
   'datatype': 'BYTES',
   'shape': [1],
   'data': [" The choice was red, green or blue. It didn't seem like an important choice when he was making it. But it was a choice nonetheless. Had he known the consequences at the time, he would likely have considered the choice a bit longer. In the end, he didn't and ended up choosing blue."]}]}